## Microsoft Building Footprints (MBF)
This is a worldwide building footprints derived from satellite imagery. Microsoft has detected 1.4B buildings from Bing Maps imagery between 2014 and 2024 including Maxar, Airbus, and IGN France imagery. The data is freely available for download and use under ODbL. 

### Data coverage
The below map shows the data coverage across the world.

```{figure} ../images/data_cov_mcsft.png
---
width: 600
name: data_cov_mcsft
---
Microsoft Building data coverage. [Source](https://github.com/microsoft/GlobalMLBuildingFootprints/blob/main/images/country-overview.png).
``` 

This dataset offers an estimation of the building height as well. However, the height attribute has a lower coverage than the footprint dataset. See below.

```{figure} ../images/building_height_cov.png
---
width: 600
name: building_height_cov
---
Microsoft Building height data coverage. [Source](https://github.com/microsoft/GlobalMLBuildingFootprints/blob/main/images/building-height-coverage.png).
``` 


### How data was created
The building extraction is done in two stages:
1. Semantic Segmentation – Recognizing building pixels on an aerial image using deep neural networks (DNNs).
2. Polygonization – Converting building pixel detections into polygons.

**Stage 1: Semantic Segmentation**

```{figure} ../images/semantic_segmentation.png
---
width: 600
name: data_cov_mcsft
---
Semantic Segmentation step.
``` 

**Stage 2: Polygonization**

```{figure} ../images/polygonization.png
---
width: 600
name: data_cov_mcsft
---
Polygonization step.
``` 

### Confidence Score
Latest releases of this dataset incorporated a confidence score between 0 and 1 that can be read as a percentage confidence. 

### Evaluation Metrics
The project provides the Precision/Recall metric for every region. 
Region | Precision | Recall
|--|--|--|
Africa|94.4%|70.9%
Caribbean|92.2%|76.8%
Central Asia|97.17%|79.47%
Europe|94.3%|85.9%
Middle East|95.7%|85.4%
South America|95.4%|78.0%
South Asia|94.8%|76.7%

The above information and more details about the project can be found in the [Project GitHub repository](https://github.com/microsoft/GlobalMLBuildingFootprints/tree/main).


### Download the data
The below code was created following the example on the Project Github repository. The goal is to download the building footprints from the area of interest, the 50 km buffer around the earthquake epicenter. 

**Step 1 - Determine which tiles intersect the AOI**

MBF stores the data in [tiles](https://learn.microsoft.com/en-us/bingmaps/articles/bing-maps-tile-system), for each tile there is a downloading link for retrieving the data. So, the first step is to find which tiles intersect with the AOI. This step can be done with the code below or using a [What the tile? tool](https://labs.mapbox.com/what-the-tile/).

In [ ]:
import pandas as pd
import mercantile
import geopandas as gpd
from shapely import geometry, Point, Polygon
import mercantile
from tqdm import tqdm
import os
import tempfile
import random
import folium

In [2]:
downloading_links = pd.read_csv('https://minedbuildings.z5.web.core.windows.net/global-buildings/dataset-links.csv', dtype=str)

In [3]:
east, south, west, north = (36.62768265193316, 37.561544985221865, 37.76386851796805, 38.460405921314695)

In [4]:
quad_keys = set()
for tile in list(mercantile.tiles(east, south, west, north, zooms=9)):
    quad_keys.add(mercantile.quadkey(tile))
quad_keys = list(quad_keys)
print(f"The input area spans {len(quad_keys)} tiles: {quad_keys}")

The input area spans 6 tiles: ['122110321', '122110302', '122110303', '122110300', '122110301', '122110320']


**Step 2 - Download the data**

Using the tiles from above, all footprints are downloaded. After that, the entire dataset is filtered to keep only buildings that lie in the AOI.

In [ ]:
# Obtain the Polygon for the Area of Interest
d = {'name': ['epicenter'], 'geometry': [Point(37.196, 38.011)]}
gdf = gpd.GeoDataFrame(d, crs="EPSG:4326")
gdf = gdf.to_crs('EPSG:23036')
gdf['buffer'] = gdf.geometry.apply(lambda x: x.buffer(50000))
gdf = gdf.set_geometry('buffer')
gdf = gdf.to_crs('EPSG:4326')
bounds = gdf.bounds.loc[0]
north, south, east, west = bounds.maxy, bounds.miny, bounds.minx, bounds.maxx
gdf.loc[1, 'name'] = 'epicenter_rectangle'
gdf.loc[1, 'buffer'] = Polygon(((east,north), (west, north), (west, south), (east, south)))

In [8]:
idx = 0
combined_gdf = gpd.GeoDataFrame()
with tempfile.TemporaryDirectory() as tmpdir:
    # Download the GeoJSON files for each tile that intersects the input geometry
    tmp_fns = []
    for quad_key in tqdm(quad_keys):
        print(quad_key)
        rows = downloading_links[downloading_links["QuadKey"] == quad_key]
        if rows.shape[0] == 1:
            url = rows.iloc[0]["Url"]

            df2 = pd.read_json(url, lines=True)
            df2["geometry"] = df2["geometry"].apply(geometry.shape)

            gdf_tile = gpd.GeoDataFrame(df2, crs=4326)
            fn = os.path.join(tmpdir, f"{quad_key}.geojson")
            tmp_fns.append(fn)
            if not os.path.exists(fn):
                gdf_tile.to_file(fn, driver="GeoJSON")
        elif rows.shape[0] > 1:
            raise ValueError(f"Multiple rows found for QuadKey: {quad_key}")
        else:
            raise ValueError(f"QuadKey not found in dataset: {quad_key}")
    # import pdb; pdb.set_trace()
    # Merge the GeoJSON files into a single file
    for fn in tmp_fns:
        gdf_tile = gpd.read_file(fn)  # Read each file into a GeoDataFrame
        gdf_tile = gdf_tile[gdf_tile.geometry.within(gdf.loc[1].buffer)]  # Filter geometries within the AOI
        gdf_tile['id'] = range(idx, idx + len(gdf_tile))  # Update 'id' based on idx
        idx += len(gdf_tile)
        combined_gdf = pd.concat([combined_gdf,gdf_tile],ignore_index=True)

  0%|                                                     | 0/6 [00:00<?, ?it/s]

122110321


 17%|███████▌                                     | 1/6 [00:07<00:37,  7.55s/it]

122110302


 33%|███████████████                              | 2/6 [00:14<00:28,  7.18s/it]

...

 67%|██████████████████████████████               | 4/6 [00:24<00:11,  5.58s/it]

122110301


 83%|█████████████████████████████████████▌       | 5/6 [00:30<00:05,  5.67s/it]

122110320


100%|█████████████████████████████████████████████| 6/6 [00:42<00:00,  7.15s/it]


**Step 3 - Explore the results**

It can be observed that all the records from this area do not have a confidence score, this means they are from a vintage dataset. 
Also, these datapoints do not have a value for the height.

The map below shows a sample of the results to consume less computation resources.


In [9]:
print('{} building footprints were retrieved'.format(len(combined_gdf)))

194264 building footprints were retrieved


In [ ]:
import json # Import json library to read a string into a dictionary

In [11]:
combined_gdf['properties'] = combined_gdf['properties'].apply(lambda x: json.loads(x))
combined_gdf['confidence'] = combined_gdf['properties'].apply(lambda x: x['confidence'])
combined_gdf['height'] = combined_gdf['properties'].apply(lambda x: x['height'])

In [12]:
combined_gdf.confidence.value_counts()

confidence
-1.0    194264
Name: count, dtype: int64

In [13]:
combined_gdf.height.value_counts()

height
-1.0    194264
Name: count, dtype: int64

In [ ]:
idx = list(combined_gdf.index)
idx_shuffled= random.shuffle(idx) # Shuffle indices to avoid spatial oversampling
m = combined_gdf.loc[idx[:1000]].explore(name = 'MBF')
gdf.loc[[1]].explore(m = m, color = 'pink', name = 'AOI')
folium.LayerControl().add_to(m)
m